## Setup

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
import requests

# ----------- Science Jubilee -------------
from science_jubilee import Machine as Jub
from science_jubilee.tools import HTTPSyringe as syringe
from science_jubilee.tools import Pipette
import time
import numpy as np

In [4]:
import logging
import contextlib
from http.client import HTTPConnection

def debug_requests_on():
    '''Switches on logging of the requests module.'''
    HTTPConnection.debuglevel = 1

    logging.basicConfig(filename = 'requestslog.log')
    logging.getLogger().setLevel(logging.DEBUG)
    requests_log = logging.getLogger("requests.packages.urllib3")
    requests_log.setLevel(logging.DEBUG)
    requests_log.propagate = True

def debug_requests_off():
    '''Switches off logging of the requests module, might be some side-effects'''
    HTTPConnection.debuglevel = 0

    root_logger = logging.getLogger()
    root_logger.setLevel(logging.WARNING)
    root_logger.handlers = []
    requests_log = logging.getLogger("requests.packages.urllib3")
    requests_log.setLevel(logging.WARNING)
    requests_log.propagate = False

In [6]:
debug_requests_on()

In [7]:
url = 'http://192.168.1.5:5000'
volume = {'volume':5}
r = requests.post(url + '/get_status', json = {'name':'1cc_2'})
r.content

send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 17\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "1cc_2"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Mon, 02 Sep 2024 23:42:41 GMT
header: Content-Type: application/json
header: Content-Length: 49
header: Connection: close


b'{"remaining_volume":null,"syringe_loaded":false}\n'

In [9]:
jubilee = Jub.Machine(address='192.168.1.2', simulated = False) 

send: b'POST /machine/code HTTP/1.1\r\nHost: 192.168.1.2\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 25\r\n\r\n'
send: b'M409 K"move.axes[].homed"'
reply: 'HTTP/1.1 500 Unknown message type or not authenticated\r\n'
header: Connection: close
send: b'GET /rr_model?key=seqs HTTP/1.1\r\nHost: 192.168.1.2\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: close\r\n\r\n'
reply: 'HTTP/1.1 200 OK\r\n'
header: Cache-Control: no-cache, no-store, must-revalidate
header: Pragma: no-cache
header: Expires: 0
header: Content-Type: application/json
header: Content-Length: 236
header: Connection: close
send: b'GET /rr_gcode?gcode=M409%20K%22move.axes%5B%5D.homed%22 HTTP/1.1\r\nHost: 192.168.1.2\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: close\r\n\r\n'
reply: 'HTTP/1.1 200 OK\r\n'
header: Cache-C

In [10]:
jubilee.home_all()

send: b'POST /machine/code HTTP/1.1\r\nHost: 192.168.1.2\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 1\r\n\r\n'
send: b'T'
reply: 'HTTP/1.1 500 Unknown message type or not authenticated\r\n'
header: Connection: close
send: b'GET /rr_model?key=seqs HTTP/1.1\r\nHost: 192.168.1.2\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: close\r\n\r\n'
reply: 'HTTP/1.1 200 OK\r\n'
header: Cache-Control: no-cache, no-store, must-revalidate
header: Pragma: no-cache
header: Expires: 0
header: Content-Type: application/json
header: Content-Length: 236
header: Connection: close
send: b'GET /rr_gcode?gcode=T HTTP/1.1\r\nHost: 192.168.1.2\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: close\r\n\r\n'
reply: 'HTTP/1.1 200 OK\r\n'
header: Cache-Control: no-cache, no-store, must-revalidate
header: Pragma:

In [11]:
deck = jubilee.load_deck('lab_automation_deck_AFL_bolton.json')

## Load labware


In [46]:
samples = jubilee.load_labware('septavialrev1_44_holder_2000ul.json', 2)
samples.manual_offset([(19.8,178.1),(132.5,177.6),(132.5,106.6)])

New manual offset applied to septavialrev1_44_holder_2000ul


In [13]:
stocks = jubilee.load_labware('20mlscintillation_12_wellplate_18000ul.json', 4)
stocks.manual_offset([(31.3,268.1),(117.6,267),(117.9,210.9)])

New manual offset applied to 20mlscintillation_12_wellplate_18000ul


In [14]:
tiprack = jubilee.load_labware('opentrons_96_tiprack_300ul.json', 0)
tiprack.manual_offset([(30.1, 77.0), (128.4, 77.4), (128.9, 14.9)])

New manual offset applied to opentrons_96_tiprack_300ul


In [15]:
trash = jubilee.load_labware('agilent_1_reservoir_290ml.json', 1)

## Load Tools

In [16]:
P300 = Pipette.Pipette.from_config(0, 'Pipette', 'P300_config.json')
jubilee.load_tool(P300)
P300.add_tiprack(tiprack)
P300.trash = trash[0]

send: b'POST /machine/code HTTP/1.1\r\nHost: 192.168.1.2\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 3\r\n\r\n'
send: b'G90'
reply: 'HTTP/1.1 500 only rr_upload is supported for POST requests\r\n'
header: Connection: close
send: b'GET /rr_model?key=seqs HTTP/1.1\r\nHost: 192.168.1.2\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: close\r\n\r\n'
reply: 'HTTP/1.1 200 OK\r\n'
header: Cache-Control: no-cache, no-store, must-revalidate
header: Pragma: no-cache
header: Expires: 0
header: Content-Type: application/json
header: Content-Length: 238
header: Connection: close
send: b'GET /rr_gcode?gcode=G90 HTTP/1.1\r\nHost: 192.168.1.2\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: close\r\n\r\n'
reply: 'HTTP/1.1 200 OK\r\n'
header: Cache-Control: no-cache, no-store, must-revalidate
header:

In [17]:
syringe_10 = syringe.HTTPSyringe.from_config(1, "../science-jubilee/src/science_jubilee/tools/configs/10cc_syringe.json")
syringe_1_1 = syringe.HTTPSyringe.from_config(2, "../science-jubilee/src/science_jubilee/tools/configs/1cc_1_syringe.json")
syringe_1_2 = syringe.HTTPSyringe.from_config(3, "../science-jubilee/src/science_jubilee/tools/configs/1cc_2_syringe.json")
syringe_1_3 = syringe.HTTPSyringe.from_config(4, "../science-jubilee/src/science_jubilee/tools/configs/1cc_3_syringe.json")

send: b'POST /get_config HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 18\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "10cc_1"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Mon, 02 Sep 2024 23:53:10 GMT
header: Content-Type: application/json
header: Content-Length: 78
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 18\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "10cc_1"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Mon, 02 Sep 2024 23:53:10 GMT
header: Content-Type: application/json
header: Content-Length: 49
header: Connection: close
send: b'POST /get_config HTTP/1.1\r\nHos

In [18]:
jubilee.load_tool(syringe_10)
jubilee.load_tool(syringe_1_1)
jubilee.load_tool(syringe_1_2)
jubilee.load_tool(syringe_1_3)

send: b'POST /machine/code HTTP/1.1\r\nHost: 192.168.1.2\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 13\r\n\r\n'
send: b'M409 K"tools"'
reply: 'HTTP/1.1 500 only rr_upload is supported for POST requests\r\n'
header: Connection: close
send: b'GET /rr_model?key=seqs HTTP/1.1\r\nHost: 192.168.1.2\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: close\r\n\r\n'
reply: 'HTTP/1.1 200 OK\r\n'
header: Cache-Control: no-cache, no-store, must-revalidate
header: Pragma: no-cache
header: Expires: 0
header: Content-Type: application/json
header: Content-Length: 238
header: Connection: close
send: b'GET /rr_gcode?gcode=M409%20K%22tools%22 HTTP/1.1\r\nHost: 192.168.1.2\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: close\r\n\r\n'
reply: 'HTTP/1.1 200 OK\r\n'
header: Cache-Control: no-cache, no-sto

In [19]:
mix_syringe = syringe_10
water_syringe = syringe_1_1
ammonia_syringe = syringe_1_2
teos_syringe = syringe_1_3

In [14]:
#water_syringe.set_pulsewidth(1350, s = 10)

## Load water syringe with water

In [20]:
water_syringe.load_syringe(600, 1500)

send: b'POST /load_syringe HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 52\r\nContent-Type: application/json\r\n\r\n'
send: b'{"volume": 600, "pulsewidth": 1500, "name": "1cc_1"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Mon, 02 Sep 2024 23:53:43 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 17\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "1cc_1"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Mon, 02 Sep 2024 23:53:43 GMT
header: Content-Type: application/json
header: Content-Length: 47
header: Connection: clo

In [21]:
water_syringe.set_pulsewidth(water_syringe.empty_position-1, s = 2000)

send: b'POST /set_pulsewidth HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 52\r\nContent-Type: application/json\r\n\r\n'
send: b'{"pulsewidth": 1844, "name": "1cc_1", "speed": 2000}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Mon, 02 Sep 2024 23:55:37 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 17\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "1cc_1"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Mon, 02 Sep 2024 23:55:37 GMT
header: Content-Type: application/json
header: Content-Length: 47
header: Connection: c

In [22]:
water_syringe.set_pulsewidth(water_syringe.full_position+1, s = 10)

send: b'POST /set_pulsewidth HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 50\r\nContent-Type: application/json\r\n\r\n'
send: b'{"pulsewidth": 1241, "name": "1cc_1", "speed": 10}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Mon, 02 Sep 2024 23:56:20 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 17\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "1cc_1"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Mon, 02 Sep 2024 23:56:20 GMT
header: Content-Type: application/json
header: Content-Length: 47
header: Connection: clo

In [23]:
water_syringe.set_pulsewidth(water_syringe.full_position+150, s = 500)

send: b'POST /set_pulsewidth HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 51\r\nContent-Type: application/json\r\n\r\n'
send: b'{"pulsewidth": 1390, "name": "1cc_1", "speed": 500}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Mon, 02 Sep 2024 23:58:38 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 17\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "1cc_1"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Mon, 02 Sep 2024 23:58:38 GMT
header: Content-Type: application/json
header: Content-Length: 47
header: Connection: cl

In [24]:
water_syringe.load_syringe(820, water_syringe.full_position+150)

send: b'POST /load_syringe HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 52\r\nContent-Type: application/json\r\n\r\n'
send: b'{"volume": 820, "pulsewidth": 1390, "name": "1cc_1"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Mon, 02 Sep 2024 23:59:14 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 17\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "1cc_1"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Mon, 02 Sep 2024 23:59:14 GMT
header: Content-Type: application/json
header: Content-Length: 47
header: Connection: clo

## Load ammonia syringe

In [17]:
#ammonia_syringe.set_pulsewidth(1420, s = 10)

In [25]:
ammonia_syringe.load_syringe(600, 1500)

send: b'POST /load_syringe HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 52\r\nContent-Type: application/json\r\n\r\n'
send: b'{"volume": 600, "pulsewidth": 1500, "name": "1cc_2"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Mon, 02 Sep 2024 23:59:19 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 17\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "1cc_2"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Mon, 02 Sep 2024 23:59:19 GMT
header: Content-Type: application/json
header: Content-Length: 47
header: Connection: clo

In [20]:
ammonia_syringe.set_pulsewidth(ammonia_syringe.empty_position-1, s = 2000)

In [27]:
ammonia_syringe.set_pulsewidth(ammonia_syringe.full_position+1, s = 2000)

send: b'POST /set_pulsewidth HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 52\r\nContent-Type: application/json\r\n\r\n'
send: b'{"pulsewidth": 1241, "name": "1cc_2", "speed": 2000}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:00:59 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 17\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "1cc_2"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:00:59 GMT
header: Content-Type: application/json
header: Content-Length: 47
header: Connection: c

In [28]:
ammonia_syringe.set_pulsewidth(ammonia_syringe.full_position+250, s = 500)

send: b'POST /set_pulsewidth HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 51\r\nContent-Type: application/json\r\n\r\n'
send: b'{"pulsewidth": 1490, "name": "1cc_2", "speed": 500}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:02:54 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 17\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "1cc_2"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:02:54 GMT
header: Content-Type: application/json
header: Content-Length: 47
header: Connection: cl

In [29]:
ammonia_syringe.load_syringe(550, ammonia_syringe.full_position+250)

send: b'POST /load_syringe HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 52\r\nContent-Type: application/json\r\n\r\n'
send: b'{"volume": 550, "pulsewidth": 1490, "name": "1cc_2"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:03:32 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 17\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "1cc_2"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:03:32 GMT
header: Content-Type: application/json
header: Content-Length: 47
header: Connection: clo

## Load TEOS syringe

In [30]:
teos_syringe.load_syringe(600, 1500)

send: b'POST /load_syringe HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 52\r\nContent-Type: application/json\r\n\r\n'
send: b'{"volume": 600, "pulsewidth": 1500, "name": "1cc_3"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:03:36 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 17\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "1cc_3"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:03:36 GMT
header: Content-Type: application/json
header: Content-Length: 47
header: Connection: clo

In [31]:
teos_syringe.set_pulsewidth(teos_syringe.empty_position-1, s = 2000)

send: b'POST /set_pulsewidth HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 52\r\nContent-Type: application/json\r\n\r\n'
send: b'{"pulsewidth": 1844, "name": "1cc_3", "speed": 2000}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:03:40 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 17\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "1cc_3"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:03:40 GMT
header: Content-Type: application/json
header: Content-Length: 47
header: Connection: c

In [32]:
teos_syringe.set_pulsewidth(teos_syringe.full_position+1, s = 200)

send: b'POST /set_pulsewidth HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 51\r\nContent-Type: application/json\r\n\r\n'
send: b'{"pulsewidth": 1241, "name": "1cc_3", "speed": 200}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:04:51 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 17\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "1cc_3"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:04:51 GMT
header: Content-Type: application/json
header: Content-Length: 47
header: Connection: cl

In [33]:
teos_syringe.set_pulsewidth(teos_syringe.full_position+200, s = 200)

send: b'POST /set_pulsewidth HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 51\r\nContent-Type: application/json\r\n\r\n'
send: b'{"pulsewidth": 1440, "name": "1cc_3", "speed": 200}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:05:36 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 17\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "1cc_3"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:05:36 GMT
header: Content-Type: application/json
header: Content-Length: 47
header: Connection: cl

In [34]:
teos_syringe.load_syringe(700, teos_syringe.full_position+200)

send: b'POST /load_syringe HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 52\r\nContent-Type: application/json\r\n\r\n'
send: b'{"volume": 700, "pulsewidth": 1440, "name": "1cc_3"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:06:05 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 17\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "1cc_3"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:06:05 GMT
header: Content-Type: application/json
header: Content-Length: 47
header: Connection: clo

In [35]:
mix_syringe.load_syringe(0, 1829)

send: b'POST /load_syringe HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 51\r\nContent-Type: application/json\r\n\r\n'
send: b'{"volume": 0, "pulsewidth": 1829, "name": "10cc_1"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:06:10 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 18\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "10cc_1"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:06:10 GMT
header: Content-Type: application/json
header: Content-Length: 45
header: Connection: clo

In [36]:
mix_syringe.set_pulsewidth(1829)

send: b'POST /set_pulsewidth HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 52\r\nContent-Type: application/json\r\n\r\n'
send: b'{"pulsewidth": 1829, "name": "10cc_1", "speed": 100}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:06:11 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 18\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "10cc_1"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 00:06:11 GMT
header: Content-Type: application/json
header: Content-Length: 45
header: Connection: 

## Experiment

##### EtOH: 1851.8 ul
##### NH3OH: 67.6 ul
##### H20: 36 ul
##### TEOS: 44.6 ul

In [39]:
etoh_fracs = [0.9804731829, 0.9609463659, 0.8437854635, 0.6875709271, 0.6094636588]
ammonia_fracs = [0.002736486486, 0.005472972973, 0.02189189189, 0.04378378378, 0.05472972973]
water_fracs = [0.005629616285, 0.01125923257, 0.04503693028, 0.09007386057, 0.1125923257]
teos_fracs = [0.01116071429, 0.02232142857, 0.08928571429, 0.1785714286, 0.2232142857]

In [45]:
target_vol = 1800
sample_volumes = []
for i in range(5):
    sample = {}
    sample['etoh'] = int(target_vol*etoh_fracs[i])
    sample['ammonia'] = int(target_vol*ammonia_fracs[i])
    sample['water'] = int(target_vol*water_fracs[i])
    sample['teos'] = int(target_vol*teos_fracs[i])

    sample_volumes.append(sample)

In [41]:
samples

[{'etoh': 1764, 'ammonia': 4, 'water': 10, 'teos': 20},
 {'etoh': 1729, 'ammonia': 9, 'water': 20, 'teos': 40},
 {'etoh': 1518, 'ammonia': 39, 'water': 81, 'teos': 160},
 {'etoh': 1237, 'ammonia': 78, 'water': 162, 'teos': 321},
 {'etoh': 1097, 'ammonia': 98, 'water': 202, 'teos': 401}]

In [35]:
target_vol = 1800

etoh_vol = target_vol*etoh_frac
ammonia_vol = target_vol*ammonia_frac
water_vol = target_vol*water_frac
teos_vol = target_vol*teos_frac

In [42]:
#etoh transfer strategy
max_trans_volume = 290


In [43]:
wash_location_1 = stocks[1]
wash_location_2 = stocks[2]

mix_vol = 2000
max_trans_volume = 290

In [50]:
def prepare_silica_precursors(sample_well, etoh_vol, water_vol, ammonia_vol):
    """
    Mix precursors (etoh, water, ammonia) at sample_well)
    """

    # transfer ethanol

    jubilee.pickup_tool(P300)
    P300.pickup_tip()

    #etoh transfer strategy ####
    

    n_full_transfers = int(np.floor(etoh_vol / max_trans_volume))
    final_etoh_vol = etoh_vol - n_full_transfers*max_trans_volume
    #########

    # etoh transfer execution
    for k in range(n_full_transfers):
        P300.aspirate(max_trans_volume, stocks[0])
        P300.dispense(max_trans_volume, sample_well.bottom(+22), s = 1000)
        time.sleep(3)
    # final transfer to hit vol
    P300.aspirate(final_etoh_vol, stocks[0])
    P300.dispense(final_etoh_vol, sample_well.bottom(+22))
    time.sleep(3)

    P300.drop_tip()
    jubilee.park_tool()


    # Transfer Ammonia
    jubilee.pickup_tool(ammonia_syringe)

    ammonia_syringe.dispense(ammonia_vol, sample_well.bottom(+20), s = 10)
    time.sleep(3)

    jubilee.park_tool()

    # Transfer water
    jubilee.pickup_tool(water_syringe)

    water_syringe.dispense(water_vol, sample_well.bottom(+20), s = 10)
    time.sleep(3)

    jubilee.park_tool()


    # mix 
    jubilee.pickup_tool(mix_syringe)
    mix_loc = samples[i].bottom(+5)
    print('mixing')
    mix_syringe.mix(mix_vol, 5, sample_well.bottom(+5), t_hold = 3, s_aspirate = 2000, s_dispense = 500)

    # wash syringe 
    mix_syringe.mix(mix_vol, 3, wash_location_1.bottom(+5), t_hold = 3, s_aspirate = 2000, s_dispense = 500)
    mix_syringe.mix(mix_vol, 3, wash_location_2.bottom(+5), t_hold = 3, s_aspirate = 2000, s_dispense = 500)

    jubilee.park_tool()




In [51]:
def add_teos(sample_well, teos_vol):

    jubilee.pickup_tool(teos_syringe)

    teos_syringe.dispense(teos_vol, sample_well.bottom(+20))
    time.sleep(3)
                          
    jubilee.park_tool()
    jubilee.pickup_tool(mix_syringe)
    

    mix_syringe.mix(mix_vol, 5, sample_well.bottom(+5), t_hold = 3, s_aspirate = 2000, s_dispense = 500)

    mix_syringe.mix(mix_vol, 3, wash_location_1, t_hold = 3, s_aspirate = 2000, s_dispense = 500)
    mix_syringe.mix(mix_vol, 3, wash_location_2, t_hold = 3, s_aspirate = 2000, s_dispense = 500)

    jubilee.park_tool()
    

In [52]:
for i, sample in enumerate(sample_volumes):
    sample_location = samples[i]
    etoh_vol = sample['etoh']
    water_vol = sample['water']
    ammonia_vol = sample['ammonia']
    teos_vol = sample['teos']
    prepare_silica_precursors(sample_location, etoh_vol, water_vol, ammonia_vol)
    add_teos(sample_location, teos_vol)

send: b'POST /machine/code HTTP/1.1\r\nHost: 192.168.1.2\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 4\r\n\r\n'
send: b'M114'
reply: 'HTTP/1.1 500 only rr_upload is supported for POST requests\r\n'
header: Connection: close
send: b'GET /rr_model?key=seqs HTTP/1.1\r\nHost: 192.168.1.2\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: close\r\n\r\n'
reply: 'HTTP/1.1 200 OK\r\n'
header: Cache-Control: no-cache, no-store, must-revalidate
header: Pragma: no-cache
header: Expires: 0
header: Content-Type: application/json
header: Content-Length: 238
header: Connection: close
send: b'GET /rr_gcode?gcode=M114 HTTP/1.1\r\nHost: 192.168.1.2\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: close\r\n\r\n'
reply: 'HTTP/1.1 200 OK\r\n'
header: Cache-Control: no-cache, no-store, must-revalidate
heade

AssertionError: Error: Syringe 1cc_3 remaining volume is 159 uL, but 401 uL dispense requested

In [53]:
jubilee.park_tool()

send: b'POST /machine/code HTTP/1.1\r\nHost: 192.168.1.2\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 4\r\n\r\n'
send: b'M114'
reply: 'HTTP/1.1 500 only rr_upload is supported for POST requests\r\n'
header: Connection: close
send: b'GET /rr_model?key=seqs HTTP/1.1\r\nHost: 192.168.1.2\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: close\r\n\r\n'
reply: 'HTTP/1.1 200 OK\r\n'
header: Cache-Control: no-cache, no-store, must-revalidate
header: Pragma: no-cache
header: Expires: 0
header: Content-Type: application/json
header: Content-Length: 246
header: Connection: close
send: b'GET /rr_gcode?gcode=M114 HTTP/1.1\r\nHost: 192.168.1.2\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: close\r\n\r\n'
reply: 'HTTP/1.1 200 OK\r\n'
header: Cache-Control: no-cache, no-store, must-revalidate
heade

In [54]:
water_syringe.set_pulsewidth(water_syringe.empty_position-1)

send: b'POST /set_pulsewidth HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 51\r\nContent-Type: application/json\r\n\r\n'
send: b'{"pulsewidth": 1844, "name": "1cc_1", "speed": 100}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 01:09:38 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 17\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "1cc_1"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 01:09:38 GMT
header: Content-Type: application/json
header: Content-Length: 47
header: Connection: cl

In [55]:
ammonia_syringe.set_pulsewidth(ammonia_syringe.empty_position-1)

send: b'POST /set_pulsewidth HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 51\r\nContent-Type: application/json\r\n\r\n'
send: b'{"pulsewidth": 1844, "name": "1cc_2", "speed": 100}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 01:10:07 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 17\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "1cc_2"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 01:10:07 GMT
header: Content-Type: application/json
header: Content-Length: 47
header: Connection: cl

In [56]:
teos_syringe.set_pulsewidth(teos_syringe.empty_position-1)

send: b'POST /set_pulsewidth HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 51\r\nContent-Type: application/json\r\n\r\n'
send: b'{"pulsewidth": 1844, "name": "1cc_3", "speed": 100}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 01:10:31 GMT
header: Content-Type: text/html; charset=utf-8
header: Content-Length: 14
header: Connection: close
send: b'POST /get_status HTTP/1.1\r\nHost: 192.168.1.5:5000\r\nUser-Agent: python-requests/2.32.3\r\nAccept-Encoding: gzip, deflate, br\r\nAccept: */*\r\nConnection: keep-alive\r\nContent-Length: 17\r\nContent-Type: application/json\r\n\r\n'
send: b'{"name": "1cc_3"}'
reply: 'HTTP/1.1 200 OK\r\n'
header: Server: Werkzeug/3.0.3 Python/3.11.2
header: Date: Tue, 03 Sep 2024 01:10:31 GMT
header: Content-Type: application/json
header: Content-Length: 47
header: Connection: cl